In [1]:
import gym
import numpy as np
rm='Pong-v0'

In [2]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')
    def animate(i):
        patch.set_data(frames[i])
    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

In [3]:
from gym.wrappers import AtariPreprocessing
gym.new_step_api=True
env = gym.make(rm)
# model initialization
H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid
model = {}
model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
model['W2'] = np.random.randn(H) / np.sqrt(H)
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
learning_rate = 1e-3
gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2
grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

def sigmoid(x): 
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  I=np.asarray(I)
  I = I[35:195] # crop
  I = I[::2,::2,0] # downsample by factor of 2
  
  I[I == 144] = 0 # erase background (background type 1)
  
  I[I == 109] = 0 # erase background (background type 2)
  
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()

def discount_rewards(r):
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  logp = np.dot(model['W2'], h)
  p = sigmoid(logp)
  return p, h # return probability of taking action 2, and hidden state

def policy_backward(epx, eph, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph.T, epdlogp).ravel()
  dh = np.outer(epdlogp, model['W2'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2}

def model_step(model, observation, prev_x):
  # preprocess the observation, set input to network to be difference image
  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x
  
  # forward the policy network and sample an action from the returned probability
  aprob, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!
  
  return action, prev_x

def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render(mode = 'rgb_array'))
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()

  prev_x = None # used in computing the difference frame
  xs,hs,dlogps,drs = [],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
    # preprocess the observation, set input to network to be difference image
    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,dlogps,drs = [],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      reward_sum = 0
      observation = env.reset() # reset env
      prev_x = None
      if episode_number == total_episodes: 
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\envs\registration.py:593: UserWarning: WARN: The environment Pong-v0 is out of date. You should consider upgrading to version `v4`.
  f"The environment {id} is out of date. You should consider "
c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\core.py:330: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  "Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future."
c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\wrappers\step_api_compatibility.py:40: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommende

In [4]:
%time hist1 = train_model(env, model, total_episodes=6000)

c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\utils\passive_env_checker.py:228: DeprecationWarning: WARN: Core environment is written in old step API which returns one bool instead of two. It is recommended to rewrite the environment with new step API. 
  "Core environment is written in old step API which returns one bool instead of two. "


episode 1.000000, reward total was -19.000000. running mean: -19.000000
episode 2.000000, reward total was -21.000000. running mean: -19.020000
episode 3.000000, reward total was -21.000000. running mean: -19.039800
episode 4.000000, reward total was -20.000000. running mean: -19.049402
episode 5.000000, reward total was -21.000000. running mean: -19.068908
episode 6.000000, reward total was -20.000000. running mean: -19.078219
episode 7.000000, reward total was -21.000000. running mean: -19.097437
episode 8.000000, reward total was -19.000000. running mean: -19.096462
episode 9.000000, reward total was -19.000000. running mean: -19.095498
episode 10.000000, reward total was -19.000000. running mean: -19.094543
episode 11.000000, reward total was -20.000000. running mean: -19.103597
episode 12.000000, reward total was -19.000000. running mean: -19.102561
episode 13.000000, reward total was -21.000000. running mean: -19.121536
episode 14.000000, reward total was -20.000000. running mean

episode 114.000000, reward total was -21.000000. running mean: -19.895326
episode 115.000000, reward total was -21.000000. running mean: -19.906372
episode 116.000000, reward total was -21.000000. running mean: -19.917309
episode 117.000000, reward total was -20.000000. running mean: -19.918135
episode 118.000000, reward total was -19.000000. running mean: -19.908954
episode 119.000000, reward total was -19.000000. running mean: -19.899865
episode 120.000000, reward total was -20.000000. running mean: -19.900866
episode 121.000000, reward total was -18.000000. running mean: -19.881857
episode 122.000000, reward total was -18.000000. running mean: -19.863039
episode 123.000000, reward total was -20.000000. running mean: -19.864408
episode 124.000000, reward total was -20.000000. running mean: -19.865764
episode 125.000000, reward total was -20.000000. running mean: -19.867107
episode 126.000000, reward total was -21.000000. running mean: -19.878436
episode 127.000000, reward total was -

episode 225.000000, reward total was -21.000000. running mean: -20.076111
episode 226.000000, reward total was -20.000000. running mean: -20.075350
episode 227.000000, reward total was -21.000000. running mean: -20.084596
episode 228.000000, reward total was -20.000000. running mean: -20.083750
episode 229.000000, reward total was -20.000000. running mean: -20.082913
episode 230.000000, reward total was -20.000000. running mean: -20.082084
episode 231.000000, reward total was -16.000000. running mean: -20.041263
episode 232.000000, reward total was -20.000000. running mean: -20.040850
episode 233.000000, reward total was -20.000000. running mean: -20.040442
episode 234.000000, reward total was -17.000000. running mean: -20.010037
episode 235.000000, reward total was -17.000000. running mean: -19.979937
episode 236.000000, reward total was -19.000000. running mean: -19.970137
episode 237.000000, reward total was -19.000000. running mean: -19.960436
episode 238.000000, reward total was -

episode 336.000000, reward total was -15.000000. running mean: -19.858853
episode 337.000000, reward total was -19.000000. running mean: -19.850265
episode 338.000000, reward total was -20.000000. running mean: -19.851762
episode 339.000000, reward total was -19.000000. running mean: -19.843244
episode 340.000000, reward total was -18.000000. running mean: -19.824812
episode 341.000000, reward total was -20.000000. running mean: -19.826564
episode 342.000000, reward total was -21.000000. running mean: -19.838298
episode 343.000000, reward total was -21.000000. running mean: -19.849915
episode 344.000000, reward total was -21.000000. running mean: -19.861416
episode 345.000000, reward total was -20.000000. running mean: -19.862802
episode 346.000000, reward total was -21.000000. running mean: -19.874174
episode 347.000000, reward total was -17.000000. running mean: -19.845432
episode 348.000000, reward total was -20.000000. running mean: -19.846978
episode 349.000000, reward total was -

...

episode 5475.000000, reward total was -3.000000. running mean: -5.026117
episode 5476.000000, reward total was -16.000000. running mean: -5.135856
episode 5477.000000, reward total was -7.000000. running mean: -5.154497
episode 5478.000000, reward total was 5.000000. running mean: -5.052952
episode 5479.000000, reward total was -5.000000. running mean: -5.052422
episode 5480.000000, reward total was -7.000000. running mean: -5.071898
episode 5481.000000, reward total was -1.000000. running mean: -5.031179
episode 5482.000000, reward total was -3.000000. running mean: -5.010867
episode 5483.000000, reward total was -7.000000. running mean: -5.030759
episode 5484.000000, reward total was -5.000000. running mean: -5.030451
episode 5485.000000, reward total was 7.000000. running mean: -4.910147
episode 5486.000000, reward total was -9.000000. running mean: -4.951045
episode 5487.000000, reward total was -11.000000. running mean: -5.011535
episode 5488.000000, reward total was 7.000000. run

episode 5588.000000, reward total was -11.000000. running mean: -4.261945
episode 5589.000000, reward total was -15.000000. running mean: -4.369326
episode 5590.000000, reward total was -5.000000. running mean: -4.375633
episode 5591.000000, reward total was -11.000000. running mean: -4.441876
episode 5592.000000, reward total was 5.000000. running mean: -4.347458
episode 5593.000000, reward total was -9.000000. running mean: -4.393983
episode 5594.000000, reward total was -5.000000. running mean: -4.400043
episode 5595.000000, reward total was -8.000000. running mean: -4.436043
episode 5596.000000, reward total was 4.000000. running mean: -4.351682
episode 5597.000000, reward total was -11.000000. running mean: -4.418166
episode 5598.000000, reward total was -7.000000. running mean: -4.443984
episode 5599.000000, reward total was -2.000000. running mean: -4.419544
episode 5600.000000, reward total was -9.000000. running mean: -4.465349
episode 5601.000000, reward total was -9.000000. 

episode 5701.000000, reward total was -9.000000. running mean: -3.834414
episode 5702.000000, reward total was -2.000000. running mean: -3.816070
episode 5703.000000, reward total was 1.000000. running mean: -3.767909
episode 5704.000000, reward total was 4.000000. running mean: -3.690230
episode 5705.000000, reward total was -2.000000. running mean: -3.673328
episode 5706.000000, reward total was 7.000000. running mean: -3.566594
episode 5707.000000, reward total was -2.000000. running mean: -3.550928
episode 5708.000000, reward total was -14.000000. running mean: -3.655419
episode 5709.000000, reward total was -2.000000. running mean: -3.638865
episode 5710.000000, reward total was -9.000000. running mean: -3.692476
episode 5711.000000, reward total was -13.000000. running mean: -3.785552
episode 5712.000000, reward total was 2.000000. running mean: -3.727696
episode 5713.000000, reward total was -6.000000. running mean: -3.750419
episode 5714.000000, reward total was 9.000000. runni

episode 5814.000000, reward total was -5.000000. running mean: -4.043714
episode 5815.000000, reward total was -7.000000. running mean: -4.073277
episode 5816.000000, reward total was 2.000000. running mean: -4.012544
episode 5817.000000, reward total was -11.000000. running mean: -4.082419
episode 5818.000000, reward total was -8.000000. running mean: -4.121594
episode 5819.000000, reward total was 4.000000. running mean: -4.040378
episode 5820.000000, reward total was -2.000000. running mean: -4.019975
episode 5821.000000, reward total was -1.000000. running mean: -3.989775
episode 5822.000000, reward total was -4.000000. running mean: -3.989877
episode 5823.000000, reward total was 6.000000. running mean: -3.889978
episode 5824.000000, reward total was -1.000000. running mean: -3.861079
episode 5825.000000, reward total was -9.000000. running mean: -3.912468
episode 5826.000000, reward total was 3.000000. running mean: -3.843343
episode 5827.000000, reward total was -7.000000. runni

episode 5927.000000, reward total was -16.000000. running mean: -3.273561
episode 5928.000000, reward total was -6.000000. running mean: -3.300825
episode 5929.000000, reward total was 7.000000. running mean: -3.197817
episode 5930.000000, reward total was -1.000000. running mean: -3.175839
episode 5931.000000, reward total was 2.000000. running mean: -3.124080
episode 5932.000000, reward total was 9.000000. running mean: -3.002840
episode 5933.000000, reward total was -4.000000. running mean: -3.012811
episode 5934.000000, reward total was -13.000000. running mean: -3.112683
episode 5935.000000, reward total was -8.000000. running mean: -3.161556
episode 5936.000000, reward total was -14.000000. running mean: -3.269941
episode 5937.000000, reward total was -15.000000. running mean: -3.387241
episode 5938.000000, reward total was 10.000000. running mean: -3.253369
episode 5939.000000, reward total was -7.000000. running mean: -3.290835
episode 5940.000000, reward total was -2.000000. r

In [5]:
play_game(env, model)

c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\core.py:52: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  "The argument mode in render method is deprecated; "
c:\users\dell\appdata\local\programs\python\python37\lib\site-packages\gym\utils\passive_env_checker.py:298: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  "No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps."


Episode finished without success, accumulated reward = 0.0
